# 1. 기본 설정

## 0) Chrome 설치

In [0]:
%%sh
set -eux
wget -q -O - https://dl.google.com/linux/linux_signing_key.pub | apt-key add -
echo "deb [arch=amd64] http://dl.google.com/linux/chrome/deb/ stable main" > /etc/apt/sources.list.d/google-chrome.list
apt-get update -y
apt-get install -y google-chrome-stable
google-chrome --version

+ wget -q -O - https://dl.google.com/linux/linux_signing_key.pub
+ apt-key add -


OK


+ echo deb [arch=amd64] http://dl.google.com/linux/chrome/deb/ stable main
+ apt-get update -y


Get:1 http://dl.google.com/linux/chrome/deb stable InRelease [1825 B]
Hit:2 https://repos.azul.com/zulu/deb stable InRelease
Hit:3 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:4 http://dl.google.com/linux/chrome/deb stable/main amd64 Packages [1212 B]
Hit:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease
Hit:6 http://security.ubuntu.com/ubuntu jammy-security InRelease
Hit:7 http://archive.ubuntu.com/ubuntu jammy-backports InRelease
Fetched 3037 B in 1s (2148 B/s)
Reading package lists...


W: http://dl.google.com/linux/chrome/deb/dists/stable/InRelease: Key is stored in legacy trusted.gpg keyring (/etc/apt/trusted.gpg), see the DEPRECATION section in apt-key(8) for details.
W: https://repos.azul.com/zulu/deb/dists/stable/InRelease: Key is stored in legacy trusted.gpg keyring (/etc/apt/trusted.gpg), see the DEPRECATION section in apt-key(8) for details.
+ apt-get install -y google-chrome-stable


Reading package lists...
Building dependency tree...
Reading state information...
The following additional packages will be installed:
  fonts-liberation libgbm1 libvulkan1 libwayland-server0 libxcb-randr0
  mesa-vulkan-drivers
The following NEW packages will be installed:
  fonts-liberation google-chrome-stable libgbm1 libvulkan1 libwayland-server0
  libxcb-randr0 mesa-vulkan-drivers
0 upgraded, 7 newly installed, 0 to remove and 40 not upgraded.
Need to get 132 MB of archives.
After this operation, 449 MB of additional disk space will be used.
Get:1 http://dl.google.com/linux/chrome/deb stable/main amd64 google-chrome-stable amd64 140.0.7339.80-1 [121 MB]
Get:2 http://archive.ubuntu.com/ubuntu jammy/main amd64 fonts-liberation all 1:1.07.4-11 [822 kB]
Get:3 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 libwayland-server0 amd64 1.20.0-1ubuntu0.1 [34.3 kB]
Get:4 http://archive.ubuntu.com/ubuntu jammy/main amd64 libxcb-randr0 amd64 1.14-3ubuntu3 [18.3 kB]
Get:5 http://archiv

debconf: delaying package configuration, since apt-utils is not installed


Fetched 132 MB in 4s (30.9 MB/s)
Selecting previously unselected package fonts-liberation.
(Reading database ... 93510 files and directories currently installed.)
Preparing to unpack .../0-fonts-liberation_1%3a1.07.4-11_all.deb ...
Unpacking fonts-liberation (1:1.07.4-11) ...
Selecting previously unselected package libwayland-server0:amd64.
Preparing to unpack .../1-libwayland-server0_1.20.0-1ubuntu0.1_amd64.deb ...
Unpacking libwayland-server0:amd64 (1.20.0-1ubuntu0.1) ...
Selecting previously unselected package libxcb-randr0:amd64.
Preparing to unpack .../2-libxcb-randr0_1.14-3ubuntu3_amd64.deb ...
Unpacking libxcb-randr0:amd64 (1.14-3ubuntu3) ...
Selecting previously unselected package libgbm1:amd64.
Preparing to unpack .../3-libgbm1_23.2.1-1ubuntu3.1~22.04.3_amd64.deb ...
Unpacking libgbm1:amd64 (23.2.1-1ubuntu3.1~22.04.3) ...
Selecting previously unselected package libvulkan1:amd64.
Preparing to unpack .../4-libvulkan1_1.3.204.1-2_amd64.deb ...
Unpacking libvulkan1:amd64 (1.3.204.

+ google-chrome --version


Google Chrome 140.0.7339.80 


## 1) 파이썬 패키지 설치 및 로드

In [0]:
%pip install --quiet selenium==4.21.0 webdriver-manager==4.0.2 beautifulsoup4==4.12.3 lxml==5.2.2 pandas==2.2.2

dbutils.library.restartPython()

Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using dbutils.library.restartPython() to use updated packages.


In [0]:
import os, re, json, time, random, pandas as pd
from urllib.parse import urljoin
from bs4 import BeautifulSoup
from datetime import datetime, timezone, timedelta
from pyspark.sql import functions as F
from pyspark.sql import types as T
import pytz

from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
from webdriver_manager.chrome import ChromeDriverManager

# 2. 크롤링 + 적재

## 0) 공통설정

### 공통 설정/함수 (드라이버 + 무한스크롤 + 상세 파서)

In [0]:
BASE = "https://jumpit.saramin.co.kr"
HEADLESS = True
DETAIL_DELAY = (0.7, 1.8)  # 요청 예절용 랜덤 대기
SEOUL = pytz.timezone("Asia/Seoul")

# 크롬 드라이버 설정
def start_driver():
    opts = Options()
    if HEADLESS:
        opts.add_argument("--headless=new")
    opts.add_argument("--no-sandbox")
    opts.add_argument("--disable-dev-shm-usage")
    opts.add_argument("--window-size=1920,1080")
    opts.add_argument("--lang=ko-KR")
    opts.add_argument("--disable-blink-features=AutomationControlled")
    opts.add_argument("user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36")
    service = Service(ChromeDriverManager().install())
    driver = webdriver.Chrome(service=service, options=opts)
    driver.set_page_load_timeout(60)
    return driver

# 무한 스크롤로 모든 공고 링크 수집
def scroll_and_collect_links_all(driver, start_url, idle_rounds=8, max_minutes=30, settle_sleep=1.2):
    driver.get(start_url)
    WebDriverWait(driver, 25).until(
        EC.presence_of_element_located((By.CSS_SELECTOR, 'div.sc-d609d44f-0.grDLmW a[href^="/position/"]'))
    )
    seen = set(); no_change = 0; t0 = time.monotonic() # 공고 url 수집용 집합 변수
    while True:
        anchors = driver.find_elements(By.CSS_SELECTOR, 'div.sc-d609d44f-0.grDLmW a[href^="/position/"]') # url 저장
        before = len(seen)
        for a in anchors:
            href = a.get_attribute("href")
            if href and href.startswith("/position/"):
                href = urljoin(BASE, href)
            if href and "/position/" in href:
                seen.add(href)

        last_h = driver.execute_script("return document.body.scrollHeight") # 스크롤 실행 전 스크롤 길이 저장
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);") # 스크롤 실행
        time.sleep(settle_sleep)
        new_h = driver.execute_script("return document.body.scrollHeight") # 스크롤 실행 후 스크롤 길이 저장

        grew_in_height = new_h > last_h
        grew_in_links = len(seen) > before
        no_change = no_change + 1 if (not grew_in_height and not grew_in_links) else 0 # 스크롤 길이 변경 여부 확인

        if no_change >= idle_rounds: # 스크롤 종료 여부 확인
            print(f"[done] 끝 도달 – {len(seen)}개 링크")
            break
        if (time.monotonic() - t0)/60 > max_minutes: # 시간 종료 여부 확인
            print(f"[warn] 시간 상한 {max_minutes}분 – {len(seen)}개 링크까지만 수집")
            break
    return list(seen) # url 리턴

# 유틸: 텍스트 정리
def clean_text(s):
    if s is None: return ""
    # 공백/줄바꿈 정리
    return re.sub(r'\n{3,}', '\n\n', re.sub(r'[ \t]+', ' ', s)).strip()

def text_from_dd(dd):
    # dd 내부가 <pre> 또는 리스트/텍스트 혼합일 수 있음
    if not dd: return ""
    # 링크의 href 텍스트도 함께 붙이기
    for a in dd.select('a[href]'):
        if a.get_text(strip=True) and a['href']:
            a.string = f"{a.get_text(strip=True)} ({a['href']})"
    txt = dd.get_text("\n", strip=True)
    return clean_text(txt)

# ---- 상세 페이지 파서 (루트: .sc-3ef60426-5.bBiQPb) ----
def parse_detail_html(html, url):
    soup = BeautifulSoup(html, "lxml")
    root = soup.select_one('.sc-3ef60426-5.bBiQPb')
    if not root:
        # 백업: 접두/접미 해시가 변할 가능성 대비
        root = soup.select_one('[class*="sc-3ef60426-"][class*="bBiQPb"], section.sc-3ef60426-5')
    if not root:
        root = soup

    # 공고명 / 기업명 / 축하금
    title = root.select_one('h1')
    company_anchor = root.select_one('a.name')
    congrats = root.select_one('[title*="취업축하금"], [class*="취업축하금"], span:contains("취업축하금")')
    공고명 = title.get_text(strip=True) if title else ""
    기업명 = company_anchor.get_text(strip=True) if company_anchor else ""
    company_href = ""
    if company_anchor and company_anchor.get("href"):
        h = company_anchor["href"]
        company_href = h if h.startswith("http") else urljoin(BASE, h)

    점핏취업축하금 = ""
    if congrats:
        점핏취업축하금 = clean_text(congrats.get_text(strip=True))

    # 주요 상세 dl (기술스택/주요업무/자격요건/우대사항/복지 및 혜택/채용절차 및 기타 지원 유의사항)
    label_map = {
        "기술스택":"기술스택",
        "주요업무":"주요업무",
        "자격요건":"자격요건",
        "우대사항":"우대사항",
        "복지 및 혜택":"복지 및 혜택",
        "채용절차 및 기타 지원 유의사항":"채용절차 및 기타 지원 유의사항",
    }
    values = {v:"" for v in label_map.values()}
    
    for dl in root.select('div.position_info dl'):
        dt = dl.select_one('dt')
        dd = dl.select_one('dd')
        if not dt or not dd: 
            continue
        key = dt.get_text(strip=True)
        if key in label_map:
            # 기술스택은 아이콘 div나 텍스트가 섞임 → 보강
            if key == "기술스택":
                chips = [clean_text(x.get_text(" ", strip=True)) for x in dd.select('[class*="sc-d9de2de1-0"], [class*="stack"], img[alt]')]
                chips = [c for c in chips if c]
                if chips:
                    values[label_map[key]] = ", ".join(dict.fromkeys(chips))  # 중복 제거 (파이썬 3.7부터 딕셔너리는 삽입 순서를 보장함. 따라서 dict.fromkeys()를 사용하면 중복을 제거하면서 원래 리스트의 요소 순서를 그대로 유지할 수 있음)
                else:
                    values[label_map[key]] = text_from_dd(dd)
            else:
                values[label_map[key]] = text_from_dd(dd)

    # 경력/학력/마감일/근무지역
    경력 = 학력 = 마감일 = 근무지역 = ""
    for dl in root.select('div.sc-b12ae455-0 dl, dl.sc-b12ae455-1'):
        dt = dl.select_one('dt')
        dd = dl.select_one('dd')
        if not dt or not dd: continue
        k = dt.get_text(strip=True)
        if k == "경력":   경력 = text_from_dd(dd)
        elif k == "학력": 학력 = text_from_dd(dd)
        elif k == "마감일": 마감일 = text_from_dd(dd)
        elif k == "근무지역":
            # li 여러 개일 수 있음
            locs = [clean_text(li.get_text(" ", strip=True)) for li in dd.select('li')]
            근무지역 = " | ".join(locs) if locs else text_from_dd(dd)
        
    collected_at = datetime.now(SEOUL).strftime("%Y-%m-%d %H:%M:%S")

    return {
        "posting_title": 공고명,
        "company_name": 기업명,
        "hiring_bonus": 점핏취업축하금,
        "posting_tech_stack": values["기술스택"],
        "responsibilities": values["주요업무"],
        "minimum_qualifications": values["자격요건"],
        "preferred_qualifications": values["우대사항"],
        "posting_benefits": values["복지 및 혜택"],
        "hiring_process": values["채용절차 및 기타 지원 유의사항"],
        "experience": 경력,
        "education": 학력,
        "end_date": 마감일,
        "work_location": 근무지역,
        "posting_url": url,
        "posting_id": (re.search(r"/position/(\d+)", url).group(1) if re.search(r"/position/(\d+)", url) else None),
        "company_url_jumpit": company_href,
        "jumpit_posting_collection_time": collected_at
    }

# ---- 상세 페이지 크롤링 ----
def crawl_detail_pages(urls, delay_range=DETAIL_DELAY):
    rows = []
    driver = start_driver() # 하나의 웹 브라우저 인스턴스를 시작
    for i, url in enumerate(urls, 1):
        try:
            driver.get(url) #현재 URL로 이동하여 페이지를 로드
            # 루트 블록 대기
            WebDriverWait(driver, 25).until(
                EC.any_of(
                    EC.presence_of_element_located((By.CSS_SELECTOR, '.sc-3ef60426-5.bBiQPb')),
                    EC.presence_of_element_located((By.CSS_SELECTOR, '[class*="sc-3ef60426-"][class*="bBiQPb"]'))
                )
            )
            html = driver.page_source #현재 페이지 HTML 소스 코드 전체 가져옴
            rows.append(parse_detail_html(html, url))
        except TimeoutException:
            rows.append({
                "posting_title": "", "company_name": "", "hiring_bonus": "", "posting_tech_stack": "",
                "responsibilities":"", "minimum_qualifications":"", "preferred_qualifications":"", "posting_benefits":"",
                "hiring_process":"", "experience":"", "education":"",
                "end_date":"", "work_location":"", "posting_url": url, "posting_id": None, "company_url_jumpit": None,
                "jumpit_posting_collection_time": None
            })  
        finally:
            time.sleep(random.uniform(*delay_range))
    driver.quit()
    return rows


In [0]:
# ---- DB 저장 ----
def insert_data(data:pd.DataFrame, schema:str, table:str, mode:str="overwrite")-> None:
    data = spark.createDataFrame(data)
    
    # 인증 정보
    jdbc_user = "postgres"
    jdbc_pass = "asdASD123!@#"

    # 연결 문자열
    host = "20.196.145.211"
    port = "5432"
    jdbc_url = f"jdbc:postgresql://{host}:{port}/postgres"

    data.write.format("jdbc").mode(mode).options(
        url=jdbc_url,
        user=jdbc_user,
        password=jdbc_pass,
        dbtable=f"{schema}.{table}"
    ).save()

%md
## 1) 직무 카테고리 정의

### 직무 카테고리 정의(1~21) + URL 빌더

In [0]:
# 직무 카테고리 매핑
JOB_CATEGORIES = {
    1: "서버/백엔드 개발자",
    2: "프론트엔드 개발자",
    3: "웹 풀스택 개발자",
    4: "안드로이드 개발자",
    5: "게임 클라이언트 개발자",
    6: "게임 서버 개발자",
    7: "DBA",
    8: "인공지능/머신러닝",
    9: "DevOps/시스템 엔지니어",
    10: "정보보안 담당자",
    11: "QA 엔지니어",
    12: "개발 PM",
    13: "HW/임베디드",
    15: "SW/솔루션",
    16: "iOS 개발자",
    17: "웹퍼블리셔",
    18: "크로스플랫폼 앱개발자",
    19: "빅데이터 엔지니어",
    20: "VR/AR/3D",
    21: "기술지원",
    22: "블록체인"
}

def build_list_url(job_cat: int) -> str:
    # 요청한 형식: ?jobCategory={id}&sort=reg_dt
    # (복수 카테고리를 동시에 묶지 않고, "직무별로 별도 크롤"을 위해 단일 카테고리만 구성)
    return f"{BASE}/positions?jobCategory={job_cat}&sort=reg_dt"

## 2) 채용공고 링크 크롤링

### 카테고리별 목록 크롤 → 체크포인트(JSON) + 목록 페이지 직무 카테고리 Delta 누적 기록

- 목적 테이블 스키마:
  - 직무카테고리 (Integer, jobCategory 값)
  - 링크 수집 시각 (Timestamp, 현재 시각)

- 각 카테고리마다 링크를 끝까지 수집하고,
  1) 해당 링크들을 JSON 체크포인트로 저장
  2) 직무카테고리/링크 수집 시각 한 줄을 Delta 테이블에 append

In [0]:
# 체크포인트 저장 디렉터리
# 체크포인트 디렉터리를 /dbfs/FileStore/jumpit_ckpt/by_category로 설정함. 이 경로는 Databricks 파일 시스템에 데이터를 저장하여 클러스터가 재시작되어도 유지됨.
ckpt_dir = "/dbfs/FileStore/jumpit_ckpt/by_category"
os.makedirs(ckpt_dir, exist_ok=True)

# 실행할 카테고리 (원하면 부분만 선택해서 실행 가능/예: [1,2,3] 등)
CATS_TO_RUN = list(JOB_CATEGORIES.keys())

rows = []  # 테이블 적재용 (직무카테고리, 링크 수집 시각)
driver = start_driver()
try:
    for cid in CATS_TO_RUN:
        list_url = build_list_url(cid)
        print(f"[{cid}] {JOB_CATEGORIES.get(cid,'')} 목록 수집 시작 → {list_url}")
        links = scroll_and_collect_links_all(
            driver, list_url,
            idle_rounds=8,    # 페이지 끝에 도달했음을 감지하는 횟수를 8회로 설정
            max_minutes=30,   #  크롤링 작업의 최대 실행 시간을 30분으로 설정
            settle_sleep=1.2  # 스크롤 후 콘텐츠가 로드될 때까지 1.2초 동안 대기
        )
        # 카테고리별 링크 체크포인트 저장
        ckpt_path = f"{ckpt_dir}/links_jobCategory_{cid}.json"
        with open(ckpt_path, "w") as f:
            json.dump(links, f, ensure_ascii=False) #ensure_ascii=True (기본값)로 저장하면 한글이 유니코드 이스케이프 코드로 변환됨
        print(f"[{cid}] 링크 {len(links)}건 저장 → {ckpt_path}")

        # Databricks 런타임 타임존 기준 (SQL current_timestamp()와 동일하게 Spark 쪽에서 찍어도 됨)
        rows.append((int(cid), datetime.now(SEOUL).strftime("%Y-%m-%d %H:%M:%S")))
finally:
    driver.quit() # 드라이버 종료(메모리 누수 방지)

[1] 서버/백엔드 개발자 목록 수집 시작 → https://jumpit.saramin.co.kr/positions?jobCategory=1&sort=reg_dt
[done] 끝 도달 – 249개 링크
[1] 링크 249건 저장 → /dbfs/FileStore/jumpit_ckpt/by_category/links_jobCategory_1.json
[2] 프론트엔드 개발자 목록 수집 시작 → https://jumpit.saramin.co.kr/positions?jobCategory=2&sort=reg_dt
[done] 끝 도달 – 142개 링크
[2] 링크 142건 저장 → /dbfs/FileStore/jumpit_ckpt/by_category/links_jobCategory_2.json
[3] 웹 풀스택 개발자 목록 수집 시작 → https://jumpit.saramin.co.kr/positions?jobCategory=3&sort=reg_dt
[done] 끝 도달 – 52개 링크
[3] 링크 52건 저장 → /dbfs/FileStore/jumpit_ckpt/by_category/links_jobCategory_3.json
[4] 안드로이드 개발자 목록 수집 시작 → https://jumpit.saramin.co.kr/positions?jobCategory=4&sort=reg_dt
[done] 끝 도달 – 31개 링크
[4] 링크 31건 저장 → /dbfs/FileStore/jumpit_ckpt/by_category/links_jobCategory_4.json
[5] 게임 클라이언트 개발자 목록 수집 시작 → https://jumpit.saramin.co.kr/positions?jobCategory=5&sort=reg_dt
[done] 끝 도달 – 6개 링크
[5] 링크 6건 저장 → /dbfs/FileStore/jumpit_ckpt/by_category/links_jobCategory_5.json
[6] 게임 서버 개발자 목록 수집 시작 → https://j

In [0]:
cols = ["job_category", "jumpit_link_collection_time"]

df = pd.DataFrame(rows, columns=cols)

for c in cols:
    if c not in df.columns:
        df[c] = None
df = df[cols]

csv_path = f"/dbfs/FileStore/jumpit_job_category.csv"
df.to_csv(csv_path, index=False)
print(f"직무 카테고리별 링크 수집 시각 CSV 저장: {csv_path}")

직무 카테고리별 링크 수집 시각 CSV 저장: /dbfs/FileStore/jumpit_job_category.csv


In [0]:
# 크롤링 결과 확인
with open('/dbfs/FileStore/jumpit_ckpt/by_category/links_jobCategory_1.json', 'r') as f:
    file_content = f.read()
print(file_content)

["https://jumpit.saramin.co.kr/position/51746001", "https://jumpit.saramin.co.kr/position/51704621", "https://jumpit.saramin.co.kr/position/51768990", "https://jumpit.saramin.co.kr/position/51583665", "https://jumpit.saramin.co.kr/position/51744578", "https://jumpit.saramin.co.kr/position/51692814", "https://jumpit.saramin.co.kr/position/51706467", "https://jumpit.saramin.co.kr/position/51582406", "https://jumpit.saramin.co.kr/position/51781050", "https://jumpit.saramin.co.kr/position/51686619", "https://jumpit.saramin.co.kr/position/51552111", "https://jumpit.saramin.co.kr/position/51525750", "https://jumpit.saramin.co.kr/position/51722528", "https://jumpit.saramin.co.kr/position/51580000", "https://jumpit.saramin.co.kr/position/51630790", "https://jumpit.saramin.co.kr/position/51629223", "https://jumpit.saramin.co.kr/position/51686583", "https://jumpit.saramin.co.kr/position/51476065", "https://jumpit.saramin.co.kr/position/51722550", "https://jumpit.saramin.co.kr/position/51741559",

In [0]:
# 크롤링 결과 확인
with open('/dbfs/FileStore/jumpit_job_category.csv', 'r') as f:
    file_content =f.read()
print(file_content)

job_category,jumpit_link_collection_time
1,2025-09-09 05:32:06.680068+00:00
2,2025-09-09 05:32:41.982028+00:00
3,2025-09-09 05:33:02.423720+00:00
4,2025-09-09 05:33:18.064410+00:00
5,2025-09-09 05:33:30.854691+00:00
6,2025-09-09 05:33:43.532168+00:00
7,2025-09-09 05:33:58.656750+00:00
8,2025-09-09 05:34:42.033407+00:00
9,2025-09-09 05:35:23.680936+00:00
10,2025-09-09 05:35:42.253918+00:00
11,2025-09-09 05:35:58.034227+00:00
12,2025-09-09 05:36:15.734991+00:00
13,2025-09-09 05:37:02.985144+00:00
15,2025-09-09 05:38:24.782329+00:00
16,2025-09-09 05:38:39.885651+00:00
17,2025-09-09 05:38:53.095085+00:00
18,2025-09-09 05:39:06.153958+00:00
19,2025-09-09 05:39:28.588344+00:00
20,2025-09-09 05:39:41.024397+00:00
21,2025-09-09 05:40:09.456673+00:00
22,2025-09-09 05:40:24.923375+00:00



### JDBC 적재: 직무 카테고리별 링크 수집 시각

In [0]:
insert_data(data=df,
            schema="bronze", 
            table="brz_jumpit_job_category",
            mode="append")

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-8993352249731270>, line 1
----> 1 insert_data(data=df,
      2             schema="bronze", 
      3             table="brz_jumpit_job_category",
      4             mode="append")

NameError: name 'insert_data' is not defined

## 3) 채용공고 상세페이지 크롤링

### 특정 직무만 상세 크롤 돌리기

직무별로 시간을 나눠 돌리고 싶다면, 위에서 저장된 카테고리별 링크 체크포인트를 불러와서 상세 크롤 함수에 넣으면 됩니다.

(기존 “채용공고 상세 페이지” 테이블 스키마를 바꾸지 않기 위해, 상세 테이블엔 카테고리 컬럼을 추가하지 않았습니다. 원하면 별도 조인 테이블로 관리하세요.)

In [0]:
# COMMAND ----------
def run_detail_for_category(cid: int, batch_size=120):
    ckpt_path = f"/dbfs/FileStore/jumpit_ckpt/by_category/links_jobCategory_{cid}.json"
    if not os.path.exists(ckpt_path):
        raise FileNotFoundError(f"체크포인트가 없습니다: {ckpt_path}  (먼저 13번 셀을 실행해 목록을 수집하세요)")

    with open(ckpt_path, "r") as f:
        links = json.load(f)
    print(f"[{cid}]번 직무 상세 크롤 시작: {len(links)}건")

    all_rows = []

    for s in range(0, len(links), batch_size):        
        part = links[s:s+batch_size]
        rows = crawl_detail_pages(part)  # 기존 상세 크롤 함수 재사용
        all_rows.extend(rows) # 크롤링으로 얻은 데이터(rows)를 all_rows 리스트에 추가
        df_part = pd.DataFrame(rows)
        part_csv = f"/dbfs/FileStore/jumpit_posting_job{cid}_part_{s//batch_size:03d}.csv"
        df_part.to_csv(part_csv, index=False)
        print(f"[{cid}] Saved part {s//batch_size:03d} → {part_csv}")

    df_all = pd.DataFrame(all_rows)
    # 기존 ‘채용공고 상세 페이지’ 스키마에 맞춰서 컬럼 순서 정렬
    cols = [
        "posting_title","company_name","hiring_bonus","posting_tech_stack","responsibilities","minimum_qualifications","preferred_qualifications",
        "posting_benefits","hiring_process","experience","education","end_date","work_location",
        "posting_url","posting_id","company_url_jumpit", "jumpit_posting_collection_time"
    ]
    # 없는 컬럼은 값 생성
    # 이 방법이 reindex()보다 속도가 더 빠르다고 함
    for c in cols:
        if c not in df_all.columns:
            df_all[c] = None # 빠지는 컬럼은 비워서라도 만들고
    df_all = df_all[cols] # 순서는 이대로
    
    # CSV 저장
    final_csv = f"/dbfs/FileStore/jumpit_posting_job{cid}_all.csv"
    df_all.to_csv(final_csv, index=False)
    print(f"[{cid}] 상세 CSV 저장: {final_csv}")

    return df_all

In [0]:
df_list = []

for i in JOB_CATEGORIES.keys():
    temp_df = run_detail_for_category(i)
    temp_df['job_category'] = i
    df_list.append(temp_df)

df_all = pd.concat(df_list, ignore_index=True)

display(df_all)

[1]번 직무 상세 크롤 시작: 249건
[1] Saved part 000 → /dbfs/FileStore/jumpit_posting_job1_part_000.csv
[1] Saved part 001 → /dbfs/FileStore/jumpit_posting_job1_part_001.csv
[1] Saved part 002 → /dbfs/FileStore/jumpit_posting_job1_part_002.csv
[1] 상세 CSV 저장: /dbfs/FileStore/jumpit_posting_job1_all.csv
[2]번 직무 상세 크롤 시작: 142건
[2] Saved part 000 → /dbfs/FileStore/jumpit_posting_job2_part_000.csv
[2] Saved part 001 → /dbfs/FileStore/jumpit_posting_job2_part_001.csv
[2] 상세 CSV 저장: /dbfs/FileStore/jumpit_posting_job2_all.csv
[3]번 직무 상세 크롤 시작: 52건
[3] Saved part 000 → /dbfs/FileStore/jumpit_posting_job3_part_000.csv
[3] 상세 CSV 저장: /dbfs/FileStore/jumpit_posting_job3_all.csv
[4]번 직무 상세 크롤 시작: 31건
[4] Saved part 000 → /dbfs/FileStore/jumpit_posting_job4_part_000.csv
[4] 상세 CSV 저장: /dbfs/FileStore/jumpit_posting_job4_all.csv
[5]번 직무 상세 크롤 시작: 6건
[5] Saved part 000 → /dbfs/FileStore/jumpit_posting_job5_part_000.csv
[5] 상세 CSV 저장: /dbfs/FileStore/jumpit_posting_job5_all.csv
[6]번 직무 상세 크롤 시작: 3건
[6] Saved par

posting_title company_name hiring_bonus posting_tech_stack responsibilities minimum_qualifications preferred_qualifications posting_benefits hiring_process experience education deadline work_location posting_url posting_id company_url_jumpit jumpit_posting_collection_time job_category 3D Scanning Application 개발(for iPad) 메디트 💰 취업축하금 50만원 SwiftUI, Xcode, vscode.dev • 3D Voxel 및 Mesh Data 핸들링
• Cloud 기반 Data 동기화 및 공유 기능 개발
• 모바일 기기에서 고성능 3D 처리 최적화 • 공학 계열 혹은 자연계열 학사 이상 (졸업 예정 포함) 또는 이에 상응하는 공학적 문제 해결 능력 보유
• SwiftUI, TCA 프레임 워크 사용 경험자
• Xcode, VSCode 개발 경험자 • 3D Scanning Application 개발 경험
• CAD/CAM 개발 경험
• 의료용 3D 이미징 시스템 개발 경험
• Voxel, Mesh를 활용하는 Application개발 경험
• Cloud 기반 데이터 동기화 Application개발 경험 • 유연근무제
• 수평적인 호칭 체계
• 최고 사양의 업무 장비/ 소프트웨어
• 웰컴키트 제공
• 캐쥬얼 복장
• 3년, 5년, 7년, 10년 이후 매 5년 근속 축하 상품권 및 휴가 제공
• 복지 포인트
• 생일 반차 및 상품권 제공
• 명절 상품권 제공
• 다양한 경조사에 대한 지원
• 종합 건강 검진
• 임직원 상해 보험 가입
• 심리상담(EAP) 지원
※ 근무지에 따라 제공되는 베네핏은 상이할 수 있습니다. [채용 절차]
서류 심사 - 1차 면접 - 2차 면접 - 처우 협의 - 최종 합격 경력 1~10년 대학교졸업(4년) 이상 null 서울 영등포구 양평로25길8, 3층, 9층, 10층, 13층, 14층, 16층 지도보기 · 주소복사 https://jumpit.saramin.co.kr/position/51746001 51746001 https://jumpit.saramin.co.kr/company/MTE0ODE5NzQ1OA==?company_nm=메디트 2025-09-09 15:00:08 1 AI Artist / Software Engineer / Full Stack 블루개러지 💰 취업축하금 50만원 AWS, GCP "Software Engineer -Full Stack" 은 AI 아티스트와 팬들이 상호작용할 수 있는 신규 모바일 서비스의 개발을 담당하여, 프론트엔드와 백엔드의 설계, 구현, 배포 및 유지보수까지 모든 과정에 참여합니다. 다양한 팀과 협력하여 AI 모델과 데이터 분석 시스템을 긴밀히 통합하고, 서비스의 안정성과 성능을 지속적으로 개선합니다.

• 크로스 플랫폼 모바일 어플리케이션의 프론트엔드 설계 및 구현
• 고성능, 고가용성의 백엔드 시스템 설계 및 개발
• AI 모델 및 데이터 분석 시스템과의 효율적이고 안정적인 통합
• 서비스의 품질과 성능을 지속적으로 모니터링하고 최적화 • 3년 이상의 개발 경력, 또는 컴퓨터 공학 연관 전공 학위
• 클라우드 환경(AWS, GCP 등) 기반 크로스 플랫폼 모바일 앱 개발/운영 경험
• 확장 가능하고 유지보수가 용이한 DB 모델링 및 쿼리 최적화 경험
• 트래픽 증가에 대응한 성능/비용 최적화 경험 • AI/ML 기술이 포함된 제품 개발 경험
• 엔터테인먼트/콘텐츠/SNS/게임 도메인의 제품 경험
• 글로벌 서비스 개발 및 운영 경험
• 제품 초기 기획부터 참여하여 구축, 운영, 모니터링까지 참여한 경험
• 수동적 업무 수행보다는 항상 '왜?'에 대해 고민하고, 고품질의 코드를 위해 끊임없이 노력하시는 분 • 인센티브 지급 : 연 1회 지급
• 최신 장비 지원 : 최신 PC 장비 및 기타 물품 지원
• 중 / 석식 및 음료 제공 : JYP BOB 중/ 석식 및 Soul Cup 카페 포인트 제공
• 복지 포인트 지급 : 명절, 창립기념일, 상/하반기 각 1회
• 경조사 및 하계휴가비 지원 : 경조금 , 경조휴가, 화환/조화, 상조회, 반려동물 경조 휴가 지원
• 장기 근속 포상 및 리프레시 휴가, 하계 휴가비 지원
• 건강 지원 : 건강검진, 독감 예방 접종 , 멘탈 케어 지원, 임직원 단체상해보험 가입
• 문화활동 지원 : 아티스트 콘서트 초대권 및 스트리밍 이용권 지원
• 유연근무제 : 선택적 근로제도, 대휴제도, 재택근무제도
• 교육비 지원
• 동호회 지원
• 휴양시설 지원
• 자녀학습지원금 지원 * 면접 대상자에게 자사 이력서 양식 제출을 요청할 수 있습니다.
* 지원서 및 제출 자료 등의 허위 사실이 확인될 경우, 채용이 취소됩니다.
* 『국가유공자 등 예우 및 지원에 관한 법률』에 의거, 취업보호 대상자는 우대합니다.
* 『장애인 고용 촉진 및 직업 재활법』에 의거, 취업보호 대상자는 우대합니다.
* 외국인의 경우 D-2(유학), D-10(구직) 비자 보유자 또는 E-7 비자 취득에 결격사유가 없어야 하며,
한국어로 의사소통이 가능한 자는 우대합니다. (한국어 능력 시험(TOPIK) 4급 이상 우대) 경력 3~15년 무관 null 서울 강동구 성안로7-13 광채빌딩 2층, Blue Garage 지도보기 · 주소복사 https://jumpit.saramin.co.kr/position/51704621 51704621 https://jumpit.saramin.co.kr/company/MzI3ODcwMjE1MQ==?company_nm=블루개러지 2025-09-09 15:00:10 1 Backend 개발자 스마트푸드네트웍스 💰 취업축하금 50만원 Java, Kotlin, Spring, QueryDSL, AWS, Git, Jira, Confluence • 외식업 매장 관리 서비스 개발
 - RESTful API, Batch 등 backend 개발
 - 자사 서비스 및 외부 인터페이스 연동 기능 개발 • Java 또는 Kotlin , Spring 기반의 웹 애플리케이션 개발 및 운영 경험 5년 이상
• JPA, QueryDSL을 활용한 데이터베이스 연동 경험
• 데이터베이스(MySQL, MongoDB 등) 에 대한 깊은 이해와 실무 경험
• AWS 환경에서의 배포 및 운영 경험
• Git을 사용한 소스 코드 관리 및 협업 경험
• Jira, Confluence 등 프로젝트 관리 도구 사용 경험 . • 시차출퇴근제도 운영
• 자율적인 연차/반차/반반차 사용
• 최신 업무 장비 및 소프트웨어 지원
• 존쿡마켓 및 존쿡 시그니처점 임직원 할인 제공
• 커피 등 음료 및 간식 지원
• 경조금 및 경조 휴가 지급
• 자녀 학자금 지원
• 생일 선물 지원
• 건강검진 지원
• 상조회 운영 서류 전형 - 1차 면접 - (필요시) 2차 면접 - 처우 협의 - 최종 합격 경력 5~15년 무관 null 서울 강남구 남부순환로2753, 3층 일부 지도보기 · 주소복사 https://jumpit.saramin.co.kr/position/51768990 51768990 https://jumpit.saramin.co.kr/company/NzE5ODcwMTc0NA==?company_nm=스마트푸드네트웍스 2025-09-09 15:00:12 1 백엔드 경력 채용 (6~9년) 텐빌리언 💰 취업축하금 50만원 Git, Spring Boot, DB • API 연동 / 오픈 소스 라이브러리 
• 프론트엔드 개발자 협업 업무
• 신규 플랫폼 개발
• Client 사이트 신규 개발
• 사이트 유지 보수 및 성능 개선 • 관련 경험 6~9년
• Backend 개발자 경험자 
• Composer 경험자
• 버전 관리 시스템 활용 가능자
• PHP 개발 경험자 • 프론트엔드 개발 언어 이해도 필요
• 워드프레스 개발 경험 
• SEO 기술 활용자 -자유로운 환경의 업무 스타일
-자유로운 연차 사용 및 시차 출퇴근
-생일 연차, 장기근속 포상금, 리조트 회원권 지원
-점

### CSV 저장

In [0]:
df_all_path = f"/dbfs/FileStore/jumpit_posting.csv"
df_all.to_csv(df_all_path, index=False)
print(f"상세 페이지 총합 CSV 저장: {df_all_path}")

상세 페이지 총합 CSV 저장: /dbfs/FileStore/jumpit_posting.csv


In [0]:
# 크롤링 결과 및 csv 저장 확인
df = pd.read_csv('/dbfs/FileStore/jumpit_posting.csv')
print(df.head())

                                posting_title  ... job_category
0        3D Scanning Application 개발(for iPad)  ...            1
1  AI Artist / Software Engineer / Full Stack  ...            1
2                                 Backend 개발자  ...            1
3                            백엔드 경력 채용 (6~9년)  ...            1
4                               안드로이드개발자(8년↑)  ...            1

[5 rows x 18 columns]


### JDBC 적재: 채용공고 상세 페이지

In [0]:
insert_data(data=df,
            schema="bronze", 
            table="brz_jumpit_posting",
            mode="overwrite")


## 4) 기업정보 상세페이지 크롤링

### 채용 상세 결과에서 기업 상세 URL 뽑기

In [0]:
urls_all = []

for cid in list(JOB_CATEGORIES.keys()):
    detail_csv = f"/dbfs/FileStore/jumpit_posting_job{cid}_all.csv"
    if not os.path.exists(detail_csv):
        raise FileNotFoundError(f"상세 CSV가 없습니다: {detail_csv}  (먼저 run_detail_for_category({cid}) 실행)")
    
    df_detail = pd.read_csv(detail_csv)
    
    urls = [u for u in df_detail.get("company_url_jumpit", []).astype(str) if u and u.startswith("http")]
    print(f"[{cid}] 기업 상세 URL {len(urls)}건")

    urls_all.extend(urls)

urls_all = sorted(set(urls_all))
print(urls_all)
#.get() 메서드 사용 이유: df['column_name']과 같은 대괄호 문법은 만약 'column_name'이 DataFrame에 없을 경우 KeyError를 발생시켜 프로그램이 중단될 수 있음
#"key": 가져오려는 열의 이름. 여기서는 "company_url_jumpit"
#"default_value": 해당 열이 존재하지 않을 때 반환될 기본값. 여기서는 **빈 리스트 []**가 설정되어 있음.

[1] 기업 상세 URL 249건
[2] 기업 상세 URL 142건
[3] 기업 상세 URL 52건
[4] 기업 상세 URL 31건
[5] 기업 상세 URL 6건
[6] 기업 상세 URL 3건
[7] 기업 상세 URL 24건
[8] 기업 상세 URL 181건
[9] 기업 상세 URL 175건
[10] 기업 상세 URL 48건
[11] 기업 상세 URL 23건
[12] 기업 상세 URL 38건
[13] 기업 상세 URL 207건
[15] 기업 상세 URL 324건
[16] 기업 상세 URL 22건
[17] 기업 상세 URL 10건
[18] 기업 상세 URL 16건
[19] 기업 상세 URL 69건
[20] 기업 상세 URL 3건
[21] 기업 상세 URL 97건
[22] 기업 상세 URL 28건
['https://jumpit.saramin.co.kr/company/MTA0ODE1NjkyMQ==?company_nm=티투엘', 'https://jumpit.saramin.co.kr/company/MTA0ODE1NzYzNA==?company_nm=쿠도커뮤니케이션', 'https://jumpit.saramin.co.kr/company/MTA0ODY1MjM0Nw==?company_nm=어센트코리아', 'https://jumpit.saramin.co.kr/company/MTA0ODYyNzc5NA==?company_nm=하이비젼시스템', 'https://jumpit.saramin.co.kr/company/MTA0ODYzMzk5NQ==?company_nm=제이티비씨', 'https://jumpit.saramin.co.kr/company/MTA1ODE1NjcyMA==?company_nm=한국비즈넷', 'https://jumpit.saramin.co.kr/company/MTA2ODE4MDg3OA==?company_nm=신보', 'https://jumpit.saramin.co.kr/company/MTA2ODE4NTYyNg==?company_nm=비욘드테크', 'https://jump

### 기업 상세 파서 & 크롤러

In [0]:
# COMMAND ----------
def only_digits(s):
    return "".join(ch for ch in s if ch.isdigit()) 
    #입력받은 문자열 s의 각 문자를 하나씩 ch 변수에 할당 
    #isdigit()는 문자가 '0'부터 '9' 사이의 숫자인 경우에만 True를 반환
    #join() 메서드는 주어진 순회 가능한 객체의 각 항목을 빈 문자열("")을 구분자로 사용하여 하나의 문자열로 결합
    #예: 채용 중인 포지션 123건 -> '1', '2', '3' -> "123"


def parse_company_html(html, url):
    soup = BeautifulSoup(html, "lxml")
    root = soup.select_one('div.sc-86740693-1.jhbtgz') \
        or soup.select_one('[class*="sc-86740693-"][class*="jhbtgz"]') \
        or soup

    # 1) 기업명
    name_el = root.select_one('section h1') or root.select_one('h1')
    기업명 = name_el.get_text(strip=True) if name_el else ""

    # 2) 기업키워드 (상단 태그 리스트)
    키워드 = []
    for li in root.select('ul.kFhGDn li, ul.sc-86740693-3 li'):
        txt = li.get_text(" ", strip=True)
        if not txt: 
            continue
        # 이모지/공백 정리
        txt = re.sub(r'^[^\w가-힣]+', '', txt).strip()
        if txt:
            키워드.append(txt)
    # 중복 제거 & JSON 문자열로 저장 (요청 포맷 예시에 맞춤)
    기업키워드 = json.dumps(list(dict.fromkeys(키워드)), ensure_ascii=False)
    #dict.fromkeys(키워드) = 키워드 리스트의 모든 요소를 딕셔너리의 키로 변환 (순서유지)     #키 값만 다시 리스트로 변환 #json.dumps()는 파이썬 객체를 JSON 형식의 문자열로 변환

    # 3) 채용 중인 포지션 수
    pos_text = ""
    more = root.select_one('#COMPANY_INFO .more')
    if more:
        pos_text = more.get_text(" ", strip=True)
    if not pos_text:
        num_el = root.select_one('#COMPANY_INGPOSITION em.num')
        pos_text = num_el.get_text(strip=True) if num_el else ""
    채용중인포지션수 = None
    m = re.search(r'(\d+)\s*건', pos_text)
    #re.search()나 re.match()와 같은 정규 표현식 함수는 패턴과 일치하는 부분을 찾으면 match object라는 객체를 반환
    if m:
        채용중인포지션수 = int(m.group(1))
        # m: 매치 객체(match object)
        #.group(1): 매치 객체의 메서드
        #.group(0) 또는 .group(): 패턴 전체와 일치하는 문자열 반환
        #.group(1): 첫 번째 캡처 그룹(첫 번째 괄호 ())과 일치하는 문자열 반환
        #.group(2): 두 번째 캡처 그룹과 일치하는 문자열 반환

    else:
        # 숫자만 있을 경우
        d = only_digits(pos_text)
        채용중인포지션수 = int(d) if d.isdigit() else None

    # 4) 업력 / 설립연도 / 주소 (COMPANY_INFO dl)
    업력 = ""
    설립연도 = ""
    주소 = ""
    company_info = root.select_one('#COMPANY_INFO dl, .ipTgkz dl')
    for div in company_info.select('div'):
        dt = div.select_one('dt')
        dd = div.select_one('dd')
        if not dt or not dd: 
            continue
        key = dt.get_text(strip=True)
        val_text = dd.get_text(" ", strip=True)
        if key == "업력":
            업력 = clean_text(val_text)
            ym = re.search(r'(\d{4})\s*년', val_text)
            if ym:
                설립연도 = ym.group(1)
        elif key in ["대표주소","주소"]:
            strong = dd.select_one('strong')
            주소 = clean_text(strong.get_text(" ", strip=True) if strong else val_text)
            #.get_text(...): 지정된 HTML 태그와 그 안에 포함된 모든 자식 태그의 텍스트 콘텐츠를 가져오는 메서
            #" " (구분자): get_text()의 여러 자식 태그의 텍스트를 하나로 합칠 때 이 구분자를 사용
            #strip=True: strip 매개변수는 텍스트의 앞뒤에 있는 불필요한 공백이나 줄바꿈을 제거하는 옵션

    # 5) 홈페이지 URL
    홈페이지URL = ""
    # (1) dt가 '홈페이지'인 경우 우선
    for dl in root.select('#COMPANY_INFO dl'):
        dt = dl.select_one('dt')
        dd = dl.select_one('dd')
        if dt and dd and "홈페이지" in dt.get_text(strip=True):
            a = dd.select_one('a[href^="http"]')
            #.select_one(...): Beautiful Soup의 메서드로, 주어진 CSS 선택자와 일치하는 첫 번째 요소를 찾아 반환
            #'a[href^="http"]': 이것이 바로 CSS 속성 선택자
            #a: <a> 태그(앵커, 링크)를 선택합니다.
            #[href^="..."]: href 속성이 특정 문자열로 시작하는 요소를 선택하는 문법
            #"http": href 속성이 "http" (또는 "https")로 시작하는 것을 의미
            
            if a:
                홈페이지URL = a["href"].strip()
                break
            #a: 이 변수는 앞선 select_one() 코드를 통해 찾은 <a ...> HTML 태그를 나타내는 Beautiful Soup 객체
            # a["href"]: 파이썬 딕셔너리와 유사한 문법으로, a 객체에서 href라는 속성의 값을 가져옴. 예를 들어, <a href="https://example.com" ...> 태그에서 a["href"]는 "https://example.com"이라는 문자열을 반환

    # (2) 대체: 점핏 외부 도메인 첫번째 링크 사용
    if not 홈페이지URL:
        for a in root.select('a[href^="http"]'):
            href = a.get("href","")
            if href and "jumpit" not in href:
                홈페이지URL = href #홈페이지 주소 없으면 지도 주소라도 들어갈 듯
                break #하나만 찾으면 넘김

    # 6) 기술스택 (COMPANY_TECHSTACK)
    techs = [clean_text(x.get_text(" ", strip=True)) 
             for x in root.select('#COMPANY_TECHSTACK .stack_wrap [class*="sc-d9de2de1-0"], #COMPANY_TECHSTACK .stack_wrap div')]
    890#이 리스트에는 빈 문자열이나 중복된 값이 포함될 수 있음

    techs = [t for t in techs if t] #리스트에서 비어 있는 값("", None 등) 제거
    기술스택 = ", ".join(dict.fromkeys(techs)) #딕셔너리로 만들어 중복 제거. dict.fromkeys()가 반환한 딕셔너리({'Python': None, 'Java': None})의 키들을 가져와 쉼표와 공백(",")으로 연결하여 하나의 문자열로 만듦

    # 7) 복지 및 혜택
    복지및혜택 = ""
    # 회사 페이지에는 별도 섹션명이 다를 수 있어 헤더 탐색
    welfare_section = None
    for sec in root.select('section'):
        h2 = sec.select_one('h2')
        if h2 and ("복지" in h2.get_text(strip=True) or "혜택" in h2.get_text(strip=True)):
            welfare_section = sec
            break
    if welfare_section:
        # 리스트/문단/태그 텍스트 취합
        txts = []
        for node in welfare_section.select('li, dd, p, pre, div'):
            t = node.get_text("\n", strip=True)
            if t:
                txts.append(t)
        if txts:
            복지및혜택 = clean_text("\n".join(txts)) #txts 리스트의 모든 항목을 줄바꿈 문자(\n)로 연결하여 하나의 큰 문자열로 만듦. 

    collected_at = datetime.now(SEOUL).strftime("%Y-%m-%d %H:%M:%S")

    return {
        "company_name": 기업명,
        "company_keywords_jumpit": 기업키워드,   # JSON 문자열 형태
        "active_positions": 채용중인포지션수,
        "years_in_business": 업력,
        "founded_year": 설립연도,
        "address": 주소,
        "homepage_url": 홈페이지URL,
        "company_tech_stack": 기술스택,
        "company_benefits": 복지및혜택,
        "company_url_jumpit": url,
        "jumpit_company_collection_time": collected_at
    }

def crawl_company_pages(urls, delay_range=DETAIL_DELAY):
    rows = []
    driver = start_driver() #Selenium 드라이버 인스턴스 시작
    for i, url in enumerate(urls, 1):
        try:
            driver.get(url) #현재 URL로 이동하여 페이지를 로드
            WebDriverWait(driver, 25).until(
                EC.any_of(
                    EC.presence_of_element_located((By.CSS_SELECTOR, 'div.sc-86740693-1.jhbtgz')),
                    EC.presence_of_element_located((By.CSS_SELECTOR, '[class*="sc-86740693-"][class*="jhbtgz"]'))
                )
            ) #페이지의 핵심 요소가 로드될 때까지 최대 25초 대기
            rows.append(parse_company_html(driver.page_source, url))
            #현재 페이지의 HTML 소스를 가져와 parse_company_html 함수로 전달
        except TimeoutException:
            rows.append({
                "company_name":"", "company_keywords_jumpit":"[]", "active_positions":None, "years_in_business":"", "founded_year":"",
                "address":"", "homepage_url":"", "company_tech_stack":"", "company_benefits":"", "company_url_jumpit":url, "jumpit_company_collection_time":""
            })
        finally:
            time.sleep(random.uniform(*delay_range))
            #*delay_range: 언패킹 연산자(unpacking operator). delay_range 변수는 (0.7, 1.5)와 같은 튜플 형태로 되어 있는데, *를 붙이면 튜플의 요소들이 개별 인자로 풀려서 random.uniform() 함수에 전달됨
    driver.quit()
    return rows


CSV와 SQL 테이블에서의 데이터 형식 문제

- 데이터를 CSV 파일이나 SQL 테이블에 저장할 때, 각 셀은 일반적으로 하나의 단일 값을 저장하도록 설계되어 있습니다.

  - 리스트를 그대로 저장하면: ['Java', 'Python', 'Docker']와 같은 Python 리스트 객체를 CSV 파일이나 SQL 테이블의 한 셀에 직접 저장할 수 없습니다. 데이터베이스는 이를 인식하지 못하고 오류를 발생시키거나, 객체 주소와 같은 알 수 없는 값으로 변환할 수 있습니다.

  - JSON 문자열로 변환하면: json.dumps() 함수는 Python 리스트를 '["Java", "Python", "Docker"]'와 같은 단일 문자열로 변환합니다. 이렇게 하면 데이터베이스나 CSV 파일은 이 값을 하나의 텍스트로 인식하고 정상적으로 저장할 수 있습니다.

- JSON 문자열은 여러 개의 값을 하나의 셀에 효율적이고 표준적인 방식으로 저장할 수 있게 해주는 "데이터 직렬화" 방법입니다. 이 덕분에 나중에 데이터를 다시 불러올 때도 json.loads() 함수를 사용하여 원래의 리스트 형태로 쉽게 복원할 수 있습니다.

### 기업 상세 전량 크롤링 → CSV/Delta 저장

In [0]:
# COMMAND ----------
# 기업 상세 크롤링
company_rows = crawl_company_pages(urls_all)
cdf = pd.DataFrame(company_rows)

# 스키마/컬럼 순서 정렬
company_cols = [
    "company_name","company_keywords_jumpit","active_positions","years_in_business","founded_year","address","homepage_url","company_tech_stack","company_benefits","company_url_jumpit", "jumpit_company_collection_time"
]
cdf = cdf.reindex(columns=company_cols) #열 인덱스 정렬

display(cdf)
print("총 기업 수:", len(cdf))

# CSV 저장
company_csv = "/dbfs/FileStore/jumpit_company.csv"
cdf.to_csv(company_csv, index=False)
print("기업 상세 페이지 CSV 저장:", company_csv)

company_name company_keywords_jumpit active_positions years_in_business founded_year address homepage_url company_tech_stack company_benefits company_url_jumpit jumpit_company_collection_time 티투엘 ["급성장중"] 5.0 26 년차 ( 2000년 9월 설립 ) 2000 경기 고양시 덕양구 향동로 201 GL메트로시티향동 B동 1314호 https://m.map.naver.com/search2/search.nhn?query=경기 고양시 덕양구 향동로 201 GL메트로시티향동 B동 1314호#/map Java • 연차사용 촉진제를 실시하여 본인이 원하는 때에 휴가를 사용할 수 있습니다.
• 장거리 근무시에는 충분한 교통비를 제공합니다.
• 야근시에는 저녁식사를 제공합니다. https://jumpit.saramin.co.kr/company/MTA0ODE1NjkyMQ==?company_nm=티투엘 2025-09-09 16:24:57 쿠도커뮤니케이션 ["매출액 500억 기업"] 16.0 26 년차 ( 2000년 10월 설립 ) 2000 경기 과천시 과천대로7나길 9, 12층 (갈현동,디엑스타워) https://m.map.naver.com/search2/search.nhn?query=경기 과천시 과천대로7나길 9, 12층 (갈현동,디엑스타워)#/map CSS 3, Java, AngularJS, Oracle PL/SQL, PostgreSQL, Headless UI, React, SQL, Jenkins, REST API, Apache Sling, XML, JavaScript, HTML5, MongoDB, Oracle, Adobe Target 단축 근무제도
열심히 일하는 당신!
30분 늦게 출근하세요♥
Family Day
한 달에 한 번!
금요일은 조기 퇴근
남여 휴게실 제공 (최신형 안마의자)
쉬고 싶을 때는 편하게!
프라이빗 공간에서 안마의자 이용
생일 조기 퇴근 및 생일 상품권 제공
생일 축하합니다!
소정의 상품권도 드려요
부모 부양지원금
경조사 지원
•자녀 입학축하금
쿠도 영웅 포상
장기근속포상
종합건강검진 지원
단체상해보험 가입
커피,음료 무제한 제공
샌드위치 데이
라운지 스낵바 (출출박스)
사내 동호회 활동 지원
모범사원포상
웰컴키트 지원
CUDO 행복배달
자격증 취득 축하금
00000
법인 리조트 운영
서울랜드 입장료 지원
외국어 교육/도서 구입비 지원
기념일 선물 (명절,성탄절, 정월대보름) https://jumpit.saramin.co.kr/company/MTA0ODE1NzYzNA==?company_nm=쿠도커뮤니케이션 2025-09-09 16:24:59 어센트코리아 ["연봉상승률 10% 이상", "급성장중", "장기근속 포상", "3호선 역세권 기업", "유연근무제", "평균연봉 6,000 이상"] 1.0 13 년차 ( 2013년 11월 설립 ) 2013 서울시 강남구 도산대로16길 15 용헌회관 301호 https://m.map.naver.com/search2/search.nhn?query=서울시 강남구 도산대로16길 15 용헌회관 301호#/map Airflow, CSS 3, Google BigQuery, Git, GCP, HTML5, Pandas, Selenium, Python, SQL • 복지 포인트 연 2회, 총 120만원 지급 
• 전직원 오전 8시-10시 시차 출퇴근제 운영 
• 본부별 근무 제도 운영(하이브리드 근무(사무실+재택) or 필요시 재택근무 가능) 
• 초과 근무시, 연장/야근/휴일 근무 수당 지급 
• 야근시, 식대 및 교통비 지급
• 공간 테마별 자율좌석제(카페형 오픈 공간, 개인 부스석 등 자유롭게 선택하여 근무 가능) 
• 장기 근속 포상제도 
• 리프레시 휴가제도(근속연수에 따라 유급휴가 부여) 
• 근로자 건강검진일 유급 휴가 지원 
• 명절 선물 지급 
• 생일자 특별 반차 
• 팀별 문화 회식/워크샵 운영 
• 업무 관련 도서 구입비/교육비 지원 
• 외/내부 교육 진행
• 우수 인재 해외 컨퍼런스 참가 기회 제공 https://jumpit.saramin.co.kr/company/MTA0ODY1MjM0Nw==?company_nm=어센트코리아 2025-09-09 16:25:02 하이비젼시스템 ["주거복지", "급성장중", "코스닥", "성과급/상여금", "사내 카페"] 4.0 16 년차 ( 2010년 4월 설립 ) 2010 경기 성남시 중원구 둔촌대로 527 https://m.map.naver.com/search2/search.nhn?query=경기 성남시 중원구 둔촌대로 527#/map C#, C++, Linux, FPGA, Embedded, Mfc, WPF, MCU, Python https://jumpit.saramin.co.kr/company/MTA0ODYyNzc5NA==?company_nm=하이비젼시스템 2025-09-09 16:25:03 제이티비씨 ["평균연봉 상위 10%", "장기근속 포상", "중앙 계열사", "경의선 역세권 기업", "평균연봉 7,000 이상"] 1.0 15 년차 ( 2011년 3월 설립 ) 2011 서울 마포구 상암산로 48-6 https://m.map.naver.com/search2/search.nhn?query=서울 마포구 상암산로 48-6#/map Docker, Confluence, ELK, JavaScript, MariaDB, Redis, Bitbucket, MSSQL, Jira, Python https://jumpit.saramin.co.kr/company/MTA0ODYzMzk5NQ==?company_nm=제이티비씨 2025-09-09 16:25:06 한국비즈넷 ["장기근속 포상", "자유로운 연차", "프리한 복장", "2호선 역세권 기업", "유연근무제"] 3.0 35 년차 ( 1991년 설립 ) 1991 서울시 구로구 디지털로29길 38, 301호(구로동, 에이스테크노타워3차) https://m.map.naver.com/search2/search.nhn?query=서울시 구로구 디지털로29길 38, 301호(구로동, 에이스테크노타워3차)#/map Java, Nexacro, Spring Boot, TortoiseSVN, MSSQL, Spring, React, Vue.js, REST API, Git, JavaScript, Tibero, Oracle • 직원휴게실 / 휴게실내 다과, 커피(믹스, 네스프레소머신) 비치
• 눈치보지않는 연차,반차 / 장기근속자 포상 / 자유복장
• 명절 선물 / 생일축하 선물 / 법인 리조트 회원가 이용
• 사내동호회 지원 / 사우회 운영 https://jumpit.saramin.co.kr/company/MTA1ODE1NjcyMA==?company_nm=한국비즈넷 2025-09-09 16:25:08 신보 ["매출액 5000억 기업", "5호선 역세권 기업"] 1.0 27 년차 ( 1999년 7월 설립 ) 1999 서울 마포구 백범로 235(신보빌딩) https://m.map.naver.com/search2/search.nhn?query=서울 마포구 백범로 235(신보빌딩)#/map AZURE, Linux, CISSP, Windows, CISA, AWS • 종합 건강 진단비 지원
　- 임직원 본인 및 직계가족의 질병을 조기 발견하여 치료할 수 있는 기회를 제공
• 휴양시설
　- 휴양시설을 활용할 수 있는 기회를 제공하여 구성원들이 편안한 여가생활을 즐길 수 있도록 지원
• 학자금
　- 임직원의 취학 전 자녀의 보육비 지원
• 경조사 지원
　- 임직원 또는 가족의 경조사 발생에 따른 축하 또는 위로의 의미를 전달하기 위하여 축하금/위로금/상조용품 및 휴가 부여
• 동호회 지원
　- 임직원들의 친목을 도모하고 건전한 자기계발의 기회 제공
• 기념품 지급
　- 생일, 창립기념일, 근로자의 날, 설날, 추석 등 임직원에게 기념품을 지급
• 생일파티
　- 매월 임직원의 생일을 축하하기 위한 간단한 생일파티를 진행하며, 생일자에게는 상품권 증정
• 조직문화 활동비 지원
　- 멘

총 기업 수: 421
기업 상세 페이지 CSV 저장: /dbfs/FileStore/jumpit_company.csv


In [0]:
# 크롤링 결과 및 csv 저장 확인
df = pd.read_csv("/dbfs/FileStore/jumpit_company.csv")
print(df.head())

  company_name  ... jumpit_company_collection_time
0          티투엘  ...            2025-09-09 16:24:57
1     쿠도커뮤니케이션  ...            2025-09-09 16:24:59
2       어센트코리아  ...            2025-09-09 16:25:02
3      하이비젼시스템  ...            2025-09-09 16:25:03
4        제이티비씨  ...            2025-09-09 16:25:06

[5 rows x 11 columns]


### JDBC 적재: 기업정보 상세 페이지

In [0]:
insert_data(data=df,
            schema="bronze", 
            table="brz_jumpit_company",
            mode="overwrite")

데이터 저장 방식에는 두 가지 개념이 있습니다.

1. 물리적 저장 

- (Data Storage)
spark_df.write.format("delta").save(company_delta_path)

- 이 코드는 Spark DataFrame의 내용을 실제로 디스크(클라우드 스토리지)에 Delta Lake 형식의 파일들로 저장하는 작업입니다. 이것은 마치 컴퓨터의 특정 폴더에 파일을 저장하는 것과 같습니다. 파일은 존재하지만, 쉽게 이름을 부르거나 관리할 수 있는 상태는 아닙니다.

2. 논리적 등록 

- (Table Registration)
CREATE TABLE ... LOCATION ...

- 이 코드는 물리적으로 저장된 파일들을 Spark의 카탈로그에 '테이블'로 등록하는 작업입니다. 이것은 마치 복잡한 파일 경로 대신 "기업정보"라는 간단한 별명을 부여하여, 누구나 그 별명만으로 파일을 찾고 사용할 수 있게 하는 것과 같습니다.


1. /dbfs (Databricks File System)

- Databricks가 기본적으로 제공하는 분산 파일 시스템의 마운트 지점입니다. 이는 클러스터에 연결된 클라우드 스토리지(기본적으로 S3, ADLS 등)를 추상화한 것입니다.

  - 이 설명은 /dbfs라는 경로 자체가 이미 클라우드 스토리지를 추상화하여 제공하는 논리적인 마운트 지점이라는 의미입니다. 즉, 사용자가 별도의 명령어를 실행할 필요 없이 Databricks 클러스터가 시작될 때 자동으로 생성되는 경로입니다. 사용자는 /dbfs/라는 경로를 통해 클라우드 스토리지에 접근하지만, 실제로는 Databricks의 내부 시스템이 이를 대신 처리해줍니다.

- 용도: 사용자가 파일 업로드, 라이브러리 설치, 또는 임시 데이터를 저장하는 데 편리합니다. 노트북에서 직접 파일을 관리하거나 Python의 os 모듈을 사용해 파일에 접근할 수 있습니다.


2. /mnt (Mount Point)

- /mnt는 클라우드 스토리지의 특정 위치를 Databricks 클러스터에 마운트(mount)하여 접근하는 경로입니다. 클라우드 스토리지 버킷(bucket) 또는 컨테이너를 Databricks의 로컬 파일 시스템처럼 사용할 수 있게 해줍니다.

  - 이 설명은 사용자가 직접 마운트 명령어를 실행하여 클라우드 스토리지의 특정 폴더(예: s3://my-bucket/my-folder)를 Databricks 클러스터의 특정 경로(/mnt/my-folder)에 연결하는 실제 행위를 말합니다. 이렇게 마운트하면 /mnt/my-folder라는 로컬 경로로 접근하는 것이 클라우드 스토리지의 s3://my-bucket/my-folder에 직접 접근하는 것과 동일하게 작동합니다.

- 용도: 대규모 데이터 파이프라인, 프로덕션 데이터 저장, 그리고 여러 Databricks 클러스터나 사용자가 공유하는 데이터를 관리하는 데 사용됩니다.


  - 성능: /mnt를 통해 접근하는 데이터는 일반적으로 /dbfs보다 대규모 데이터 처리에서 더 나은 성능을 보입니다. 데이터 레이크(Data Lake) 아키텍처를 구축할 때 필수적입니다.

  - 데이터 거버넌스: 마운트 지점은 보안을 위해 별도의 인증 정보를 필요로 하므로, 데이터에 대한 접근 제어가 용이합니다.

  - 명확한 목적: /mnt는 특정 비즈니스 데이터(예: s3://my-data-lake/raw-data/와 같은 경로)를 구조화하고 관리하기 위한 목적으로 사용됩니다.

#3. 테이블 확인

### Delta 쿼리 예시

In [0]:
# %sql
# -- COMMAND ----------
# SELECT 기업명,
#        TRY_CAST(`채용 중인 포지션 수` AS INT) AS 채용중_포지션수,
#        설립연도,
#        SUBSTRING(기술스택,1,120) AS 기술스택_요약
# FROM `기업정보 상세 페이지`
# ORDER BY 채용중_포지션수 DESC NULLS LAST
# LIMIT 30;

In [0]:
# # COMMAND ----------
# # 기업키워드를 배열로 펼쳐 보고 싶을 때(JSON → explode)
# from pyspark.sql.functions import from_json, col, explode, schema_of_json

# sample_json = '["연봉상승률 20% 이상","육아휴직"]'
# schema = spark.read.json(spark.createDataFrame([(sample_json,)], ["j"])).schema
# t = spark.table("`기업정보 상세 페이지`") \
#     .withColumn("기업키워드_arr", from_json(col("기업키워드"), schema["j"].dataType)) \
#     .withColumn("키워드", explode(col("기업키워드_arr")))
# display(t.select("기업명","키워드").limit(50))

#4. 250911 17:17 deadline ▶ end_date

### 저장된 배치데이터 찾아서 합치고 적재하기

In [0]:
/dbfs/FileStore/jumpit_posting_job17_part_000.csv

['000', '001', '002']

In [0]:
import pandas as pd
import glob

df_list = []
path_base = "/dbfs/FileStore/"

for cid in JOB_CATEGORIES.keys():
    try:
        print(f"'{cid}' 카테고리 파일 찾기 시작")
        
        # glob 모듈을 사용해 와일드카드(*)로 일치하는 모든 파일 경로를 가져옵니다.
        # 이렇게 하면 파일 번호를 일일이 지정할 필요가 없습니다.
        file_paths = glob.glob(f"{path_base}jumpit_posting_job{cid}_part_*.csv")
        
        if not file_paths:
            print(f"경로에 해당하는 파일이 없습니다: '{path_base}jumpit_posting_job{cid}_part_*.csv'")
            continue
        
        for path in file_paths:
            print(f"'{path}' 파일 읽기 시작")
            df = pd.read_csv(path)
            df['job_category'] = cid
            df_list.append(df)
            
    except Exception as e:
        print(f"오류 발생: {path} - {e}")
        continue

# 리스트에 모아둔 모든 DataFrame을 한 번에 병합합니다.
if df_list:
    df_merged = pd.concat(df_list, ignore_index=True)
    print("모든 파일을 성공적으로 병합했습니다.")
    print(f"총 행 수: {len(df_merged)}")
else:
    print("병합할 데이터가 없습니다.")

'1' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job1_part_000.csv' 파일 읽기 시작
'/dbfs/FileStore/jumpit_posting_job1_part_001.csv' 파일 읽기 시작
'/dbfs/FileStore/jumpit_posting_job1_part_002.csv' 파일 읽기 시작
'2' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job2_part_000.csv' 파일 읽기 시작
'/dbfs/FileStore/jumpit_posting_job2_part_001.csv' 파일 읽기 시작
'3' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job3_part_000.csv' 파일 읽기 시작
'4' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job4_part_000.csv' 파일 읽기 시작
'5' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job5_part_000.csv' 파일 읽기 시작
'6' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job6_part_000.csv' 파일 읽기 시작
'7' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job7_part_000.csv' 파일 읽기 시작
'8' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job8_part_000.csv' 파일 읽기 시작
'/dbfs/FileStore/jumpit_posting_job8_part_001.csv' 파일 읽기 시작
'9' 카테고리 파일 찾기 시작
'/dbfs/FileStore/jumpit_posting_job9_part_000.csv' 파일 읽기 시작
'/dbfs/FileStore/jumpit_posting_job9_part_001.csv' 파일 읽기 시

In [0]:
cols = [
        "posting_title","company_name","hiring_bonus","posting_tech_stack","responsibilities","minimum_qualifications","preferred_qualifications",
        "posting_benefits","hiring_process","experience","education","end_date","work_location",
        "posting_url","posting_id","company_url_jumpit", "jumpit_posting_collection_time", "job_category"
    ]

for c in cols:
    if c not in df_merged.columns:
        df_merged[c] = None
df_merged = df_merged[cols]

In [0]:
posting_csv = "/dbfs/FileStore/jumpit_posting.csv"
df_merged.to_csv(posting_csv, index=False)
print("기업 상세 페이지 CSV 저장:", posting_csv)

insert_data(data=df_merged,
            schema="bronze", 
            table="brz_jumpit_posting",
            mode="overwrite")

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-7529612058496705>, line 2
      1 posting_csv = "/dbfs/FileStore/jumpit_posting.csv"
----> 2 df_merged.to_csv(posting_csv, index=False)
      3 print("기업 상세 페이지 CSV 저장:", posting_csv)
      5 insert_data(data=df_merged,
      6             schema="bronze", 
      7             table="brz_jumpit_posting",
      8             mode="overwrite")

NameError: name 'df_merged' is not defined

#5. 250915 17:12 brz_jumpit_company.CSV 재적재

In [0]:
import pandas as pd
df = pd.read_csv("/dbfs/FileStore/jumpit_company.csv")

insert_data(data=df,
            schema="bronze", 
            table="brz_jumpit_company",
            mode="overwrite")